In [1]:
USE_SERVER = True
if USE_SERVER:
    !pip install elasticsearch
    !pip install elasticsearch_dsl
    !pip install pymed
    !pip install gensim
    !pip install torchsummary

In [2]:
from __future__ import print_function
import argparse
import numpy as np
import torch
import torch.utils.data
from torch import nn, optim
from torch.nn import functional as F
from torchvision import datasets, transforms
from torchvision.utils import save_image
import pandas as pd
import utils
import os
from utils import PROJECT_ROOT, DATA_PATH
import yuval_module.paper_source as PaperSource

from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.pipeline import Pipeline

import py_4.get_mesh_vec as get_mesh_vec
import py_3.sim_matrix_3 as sim_matrix_3
import py_4.get_all_features as get_all_features 
from sklearn.cluster import DBSCAN as DBS

from sklearn.cluster import KMeans
from sklearn.metrics import silhouette_samples, silhouette_score

import metric_eval_2


from torch.utils.data import Dataset, DataLoader

from sklearn.manifold import TSNE
%matplotlib inline
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
import seaborn as sns
import time
import pickle

from sklearn.preprocessing import StandardScaler

%load_ext autoreload
%autoreload 2

In [3]:
mesh_embed=get_mesh_vec.MeshEmbeddings(PROJECT_ROOT + "data/mesh_data/MeSHFeatureGeneratedByDeepWalk.csv")

In [4]:
FILE = "enriched_labeled_dataset_large" 
if os.path.exists(PROJECT_ROOT + DATA_PATH + FILE):
    print("READING FROM LOCAL")
    if FILE.split(".")[1] == "json":
        df = pd.read_json(PROJECT_ROOT + DATA_PATH + FILE)
    else:
        df = pd.read_csv(PROJECT_ROOT + DATA_PATH + FILE)
    #ps = PaperSource()
else:
    print("PULLING FROM S3")
    ps = sim_matrix_3.load_dataset(FILE)
    df = ps.get_dataset()

df.drop(columns=["last_author_country"],inplace=True)
df.rename(columns={'ORG_STATE':'last_author_country'},inplace=True)

print("FILE PULLED")

PULLING FROM S3
FILE PULLED


In [5]:
cd ..

/home/ubuntu/AYP


In [28]:
class VAE_A(nn.Module):
    def __init__(self, hidden_dim, latent_dim, input_dim):
        super(VAE_A, self).__init__()
        self.input_dim = input_dim
        self.hd = hidden_dim
        self.latent_dim = latent_dim
         
        self.fc1 = nn.Linear(self.input_dim, self.hd)
        self.fc21 = nn.Linear(self.hd, self.latent_dim)
        self.fc22 = nn.Linear(self.hd, self.latent_dim)
        self.fc3 = nn.Linear(self.latent_dim, self.hd)
        self.fc4 = nn.Linear(self.hd,self.input_dim)
        
        self.dropout = torch.nn.Dropout(p=0.4) 
        self.bn1 = nn.BatchNorm1d(self.hd)
        self.bn5 = nn.BatchNorm1d(self.hd)

    def encode(self, x):
        h = F.relu(self.fc1(x))
        return self.fc21(h), self.fc22(h)

    def reparameterize(self, mu, logvar):
        std = torch.exp(0.5*logvar)
        eps = torch.randn_like(std)
        return eps.mul(std).add_(mu) # return z sample
        

    def decode(self, z):
        h = F.relu(self.fc3(z))
        return self.fc4(h)

    def forward(self, x):
        mu, logvar = self.encode(x.view(-1, self.input_dim))
        z = self.reparameterize(mu, logvar)
        return self.decode(z), mu, logvar

In [42]:
class ToyDS(Dataset):
    def __init__(self,df,selection,vae_features = None):
        super().__init__()
        self.df = df[df['last_author_name'].isin(selection)]
        if vae_features is None:
            print("Creating new VAE FEATURES")
            self.vae_features = get_all_features.VAE_Features(self.df)
        else:
            print("Using pre-defined VAE FEATURES")
            self.vae_features = vae_features
        self.features = self.vae_features.get_all_features(self.df)
#         print(list(self.vae_features.mesh_features.mesh_missing))
        self.input_dim = self.vae_features.input_dims
            
    def __len__(self):
        return self.df.shape[0]
    
    def __getitem__(self, idx):
        features = self.features[idx]
        return features
    
    def __getvae__(self):
        return self.vae_features

In [44]:
MODEL_PATH = "./code/models/vae_a_8dim_allfeat.pt"

model = torch.load(MODEL_PATH)
model.eval()

VAE_A(
  (fc1): Linear(in_features=1099, out_features=32, bias=True)
  (fc21): Linear(in_features=32, out_features=8, bias=True)
  (fc22): Linear(in_features=32, out_features=8, bias=True)
  (fc3): Linear(in_features=8, out_features=32, bias=True)
  (fc4): Linear(in_features=32, out_features=1099, bias=True)
)

In [45]:
with open('./code/models/vae_allfeat.pkl', 'rb') as input:
    vae_feat = pickle.load(input)

In [46]:
auth_eps = pd.read_csv("data/val_set_author_names.csv")["0"]
auth_usecase = pd.read_csv("data/test_set_author_names.csv")["0"]

### HYPERPARAMETER OPTIMIZATION ###

In [23]:
#settings

BATCH_SIZE= 32
EPOCHS = 30
cuda = torch.cuda.is_available()
seed = 42
log_interval = 10
num_workers = 2

#check for cuda
device = torch.device('cuda' if cuda else 'cpu')

torch.manual_seed(seed)
kwargs = {'num_workers': 1, 'pin_memory': True} if cuda else {}

device

device(type='cuda')

In [46]:
db__eps = np.linspace(.40,.60,40)

best_eps = None
best_f1 = 0.0

sil_score_log = {}

for db_eps in db__eps:
    df_all_cases = []

    for auth in auth_eps:
        df_auth = df[df['last_author_name'] == auth] 
        data = ToyDS(df,[auth], vae_features = vae_feat)
        data = torch.from_numpy(data.features).to(device,dtype=torch.float32)
        _, mu, __ = model(data)
        latent_feat = mu.detach().cpu().numpy()
        df_all_cases.append([df_auth,latent_feat])
        
    y_hat_comb = []

    for case in df_all_cases:
        df_clus, latent_feat = case
        y_hat = DBS(eps=db_eps,min_samples=1,metric="euclidean").fit(latent_feat)
        df_clus = df_clus[["pmid","PI_IDS"]]
        df_clus['cluster_pred'] = y_hat.labels_
        y_hat_comb.append(df_clus)

        
    f1, precision, recall, df_eval = metric_eval_2.get_metrics_many(y_hat_comb)

    if f1 > best_f1:
        best_f1 = f1
        best_eps = db_eps

Using pre-defined VAE FEATURES
['MESH NAME NOT FOUND: Infections', 'MESH NAME NOT FOUND: Lactate Dehydrogenase 5', 'MESH NAME NOT FOUND: Phospholipid Hydroperoxide Glutathione Peroxidase', 'MESH NAME NOT FOUND: Stimuli Responsive Polymers', "MESH NAME NOT FOUND: Practice Patterns, Nurses'", 'MESH NAME NOT FOUND: Psychology, Positive', 'MESH NAME NOT FOUND: Female', 'MESH NAME NOT FOUND: Gingipain Cysteine Endopeptidases', 'MESH NAME NOT FOUND: Protein-Arginine Deiminase Type 4', 'MESH NAME NOT FOUND: Psychological Distress', 'MESH NAME NOT FOUND: Copper-Transporting ATPases', 'MESH NAME NOT FOUND: Indigenous Peoples', 'MESH NAME NOT FOUND: Sphingosine-1-Phosphate Receptors', 'MESH NAME NOT FOUND: Broadly Neutralizing Antibodies', 'MESH NAME NOT FOUND: Outcome Assessment, Health Care', 'MESH NAME NOT FOUND: Recognition, Psychology', 'MESH NAME NOT FOUND: Outcome and Process Assessment, Health Care', 'MESH NAME NOT FOUND: Illicit Drugs', 'MESH NAME NOT FOUND: RNA, Circular', 'MESH NAME N

/home/ubuntu/AYP/code/py_4/get_all_features.py:83: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['co_authors']=df.authors.apply( lambda x: [i['name'] for i in x] )
/home/ubuntu/AYP/code/py_4/get_all_features.py:83: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['co_authors']=df.authors.apply( lambda x: [i['name'] for i in x] )
/home/ubuntu/AYP/code/py_4/get_all_features.py:83: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_inde

Using pre-defined VAE FEATURES
['MESH NAME NOT FOUND: Infections', 'MESH NAME NOT FOUND: Lactate Dehydrogenase 5', 'MESH NAME NOT FOUND: Phospholipid Hydroperoxide Glutathione Peroxidase', 'MESH NAME NOT FOUND: Stimuli Responsive Polymers', "MESH NAME NOT FOUND: Practice Patterns, Nurses'", 'MESH NAME NOT FOUND: Psychology, Positive', 'MESH NAME NOT FOUND: Female', 'MESH NAME NOT FOUND: Gingipain Cysteine Endopeptidases', 'MESH NAME NOT FOUND: Protein-Arginine Deiminase Type 4', 'MESH NAME NOT FOUND: Psychological Distress', 'MESH NAME NOT FOUND: Copper-Transporting ATPases', 'MESH NAME NOT FOUND: Indigenous Peoples', 'MESH NAME NOT FOUND: Sphingosine-1-Phosphate Receptors', 'MESH NAME NOT FOUND: Broadly Neutralizing Antibodies', 'MESH NAME NOT FOUND: Outcome Assessment, Health Care', 'MESH NAME NOT FOUND: Recognition, Psychology', 'MESH NAME NOT FOUND: Outcome and Process Assessment, Health Care', 'MESH NAME NOT FOUND: Illicit Drugs', 'MESH NAME NOT FOUND: RNA, Circular', 'MESH NAME N

/home/ubuntu/AYP/code/py_4/get_all_features.py:83: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['co_authors']=df.authors.apply( lambda x: [i['name'] for i in x] )
/home/ubuntu/AYP/code/py_4/get_all_features.py:83: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['co_authors']=df.authors.apply( lambda x: [i['name'] for i in x] )
/home/ubuntu/AYP/code/py_4/get_all_features.py:83: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_inde

Using pre-defined VAE FEATURES
['MESH NAME NOT FOUND: Infections', 'MESH NAME NOT FOUND: Lactate Dehydrogenase 5', 'MESH NAME NOT FOUND: Phospholipid Hydroperoxide Glutathione Peroxidase', 'MESH NAME NOT FOUND: Stimuli Responsive Polymers', "MESH NAME NOT FOUND: Practice Patterns, Nurses'", 'MESH NAME NOT FOUND: Psychology, Positive', 'MESH NAME NOT FOUND: Female', 'MESH NAME NOT FOUND: Gingipain Cysteine Endopeptidases', 'MESH NAME NOT FOUND: Protein-Arginine Deiminase Type 4', 'MESH NAME NOT FOUND: Psychological Distress', 'MESH NAME NOT FOUND: Copper-Transporting ATPases', 'MESH NAME NOT FOUND: Indigenous Peoples', 'MESH NAME NOT FOUND: Sphingosine-1-Phosphate Receptors', 'MESH NAME NOT FOUND: Broadly Neutralizing Antibodies', 'MESH NAME NOT FOUND: Outcome Assessment, Health Care', 'MESH NAME NOT FOUND: Recognition, Psychology', 'MESH NAME NOT FOUND: Outcome and Process Assessment, Health Care', 'MESH NAME NOT FOUND: Illicit Drugs', 'MESH NAME NOT FOUND: RNA, Circular', 'MESH NAME N

...

['MESH NAME NOT FOUND: Infections', 'MESH NAME NOT FOUND: Lactate Dehydrogenase 5', 'MESH NAME NOT FOUND: Phospholipid Hydroperoxide Glutathione Peroxidase', 'MESH NAME NOT FOUND: Stimuli Responsive Polymers', "MESH NAME NOT FOUND: Practice Patterns, Nurses'", 'MESH NAME NOT FOUND: Psychology, Positive', 'MESH NAME NOT FOUND: Female', 'MESH NAME NOT FOUND: Gingipain Cysteine Endopeptidases', 'MESH NAME NOT FOUND: Protein-Arginine Deiminase Type 4', 'MESH NAME NOT FOUND: Psychological Distress', 'MESH NAME NOT FOUND: Copper-Transporting ATPases', 'MESH NAME NOT FOUND: Indigenous Peoples', 'MESH NAME NOT FOUND: Sphingosine-1-Phosphate Receptors', 'MESH NAME NOT FOUND: Broadly Neutralizing Antibodies', 'MESH NAME NOT FOUND: Outcome Assessment, Health Care', 'MESH NAME NOT FOUND: Recognition, Psychology', 'MESH NAME NOT FOUND: Outcome and Process Assessment, Health Care', 'MESH NAME NOT FOUND: Illicit Drugs', 'MESH NAME NOT FOUND: RNA, Circular', 'MESH NAME NOT FOUND: Inhibition, Psycholog

/home/ubuntu/AYP/code/py_4/get_all_features.py:83: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['co_authors']=df.authors.apply( lambda x: [i['name'] for i in x] )
/home/ubuntu/AYP/code/py_4/get_all_features.py:83: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['co_authors']=df.authors.apply( lambda x: [i['name'] for i in x] )
/home/ubuntu/AYP/code/py_4/get_all_features.py:83: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_inde

['MESH NAME NOT FOUND: Infections', 'MESH NAME NOT FOUND: Lactate Dehydrogenase 5', 'MESH NAME NOT FOUND: Phospholipid Hydroperoxide Glutathione Peroxidase', 'MESH NAME NOT FOUND: Stimuli Responsive Polymers', "MESH NAME NOT FOUND: Practice Patterns, Nurses'", 'MESH NAME NOT FOUND: Psychology, Positive', 'MESH NAME NOT FOUND: Female', 'MESH NAME NOT FOUND: Gingipain Cysteine Endopeptidases', 'MESH NAME NOT FOUND: Protein-Arginine Deiminase Type 4', 'MESH NAME NOT FOUND: Psychological Distress', 'MESH NAME NOT FOUND: Copper-Transporting ATPases', 'MESH NAME NOT FOUND: Indigenous Peoples', 'MESH NAME NOT FOUND: Sphingosine-1-Phosphate Receptors', 'MESH NAME NOT FOUND: Broadly Neutralizing Antibodies', 'MESH NAME NOT FOUND: Outcome Assessment, Health Care', 'MESH NAME NOT FOUND: Recognition, Psychology', 'MESH NAME NOT FOUND: Outcome and Process Assessment, Health Care', 'MESH NAME NOT FOUND: Illicit Drugs', 'MESH NAME NOT FOUND: RNA, Circular', 'MESH NAME NOT FOUND: Inhibition, Psycholog

/home/ubuntu/AYP/code/py_4/get_all_features.py:83: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['co_authors']=df.authors.apply( lambda x: [i['name'] for i in x] )
/home/ubuntu/AYP/code/py_4/get_all_features.py:83: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['co_authors']=df.authors.apply( lambda x: [i['name'] for i in x] )
/home/ubuntu/AYP/code/py_4/get_all_features.py:83: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_inde

KeyboardInterrupt: 

In [ ]:
print(best_eps)
print(best_f1)

### GET SCORES FROM USE CASES

In [54]:
def pipeline_vae_db(df,authors,eps):
    
    df_all_cases = []

    for i,auth in enumerate(authors):
        print("Processing combination number {} from {}".format(i+1,num_cases))
        df_auth = df[df['last_author_name'] == auth]
        #Calculate the distance matrix
        
        df_auth = df[df['last_author_name'] == auth] 
        data = ToyDS(df, [auth], vae_features = vae_feat)
        data = torch.from_numpy(data.features).to(device,dtype=torch.float32)
        _, mu, __ = model(data)
        latent_feat = mu.detach().cpu().numpy()
        df_all_cases.append([df_auth,latent_feat])

    y_hat_comb = []
    
    for case in df_all_cases:
        df_clus, latent_feat = case
        y_hat = DBS(eps=db_eps,min_samples=1,metric="euclidean").fit(latent_feat)
        df_clus = df_clus[["pmid","PI_IDS"]]
        df_clus['cluster_pred'] = y_hat.labels_
        y_hat_comb.append(df_clus)
    
    return y_hat_comb

In [30]:
def pipeline_vae_kmeans(df,auth_df,authors,use_case):
    
    if use_case == "1_da" or use_case == "mix_bag":
        authors = sim_matrix_3.get_use_case(df,use_case)
    else:
        auth_df = df[df['last_author_name'].isin(authors)]   
        authors = sim_matrix_3.get_use_case(auth_df,use_case)
        
    num_cases = len(authors)
    
    df_all_cases = []
    all_papers = []

    for i,auth in enumerate(authors):
        print("Processing combination number {} from {}".format(i+1,num_cases))
        df_auth = df[df['last_author_name'] == auth]
        all_papers.append(df_auth.shape[0])
        #Calculate the distance matrix
        
        df_auth = df[df['last_author_name'] == auth] 
        data = ToyDS(df, [auth], vae_features = vae_feat)
        data = torch.from_numpy(data.features).to(device,dtype=torch.float32)
        _, mu, __ = model(data)
        latent_feat = mu.detach().cpu().numpy()
        df_all_cases.append([df_auth,latent_feat])

    y_hat_comb = []
    
    for case in df_all_cases:
        df_clus, latent_feat = case
        
        
        
#         y_hat = DBS(eps=db_eps,min_samples=1,metric="euclidean").fit(latent_feat)
        range_n_clusters = np.arange(1,11)
        best_score = 0.0
        best_n = None
        best_labels = None
        for n_clusters in range_n_clusters:
            clusterer = KMeans(n_clusters=n_clusters, random_state=10)
            cluster_labels = clusterer.fit_predict(latent_feat)
            print(cluster_labels)
            silhouette_avg = silhouette_score(latent_feat, cluster_labels)
            sil_score_log[n_clusters] = silhouette_avg
            if silhouette_avg > best_score:
                best_score = silhouette_avg
                best_n = n_clusters
                best_labels = cluster_labels
        
        df_clus = df_clus[["pmid","PI_IDS"]]
        df_clus['cluster_pred'] = best_labels.labels_
        y_hat_comb.append(df_clus)
    
    return y_hat_comb, num_cases, np.mean(np.array(all_papers))

In [12]:
all_usecase_auth = list(pd.read_csv("./data/test_set_author_names.csv").drop(columns=["Unnamed: 0"])["0"])
df_usecase = df[df['last_author_name'].isin(all_usecase_auth)]

In [19]:
auth_1 = pd.read_csv("./data/one_da_usecase_author_names.csv").drop(columns=["Unnamed: 0"])["0"]
auth_2_same = sim_matrix_3.get_use_case(df_usecase,"2_da_same")
auth_2_dif = sim_matrix_3.get_use_case(df_usecase,"2_da_dif")
auth_3 = sim_matrix_3.get_use_case(df_usecase,"3_da")

In [29]:
dict_allcases = {}
dict_allcases['2_da_same'] = auth_2_same
dict_allcases['2_da_dif'] = auth_2_dif
dict_allcases['3_da'] = auth_3
dict_allcases['1_da'] = auth_1

In [33]:
total_authors = list(auth_2_same) + list(auth_2_dif) + list(auth_3) + list(auth_1)

In [138]:
total_metric = []
use_cases = ['2_da_same','2_da_dif','3_da', '1_da']

for case in use_cases:
    y_hat_comb = pipeline_vae_db(df,authors=dict_allcases[case],eps=1.975)
    f1, precision, recall, df_eval = metric_eval_2.get_metrics_many(y_hat_comb)
    total_metric.append([case,f1,precision,recall,df_eval])

Processing combination number 1 from 50
Using pre-defined VAE FEATURES
Processing combination number 2 from 50
Using pre-defined VAE FEATURES
Processing combination number 3 from 50
Using pre-defined VAE FEATURES
Processing combination number 4 from 50
Using pre-defined VAE FEATURES
Processing combination number 5 from 50


/home/ubuntu/AYP/code/py_4/get_all_features.py:92: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['co_authors']=df.authors.apply(lambda x: [i['name'].lower().split(",") for i in x] )
/home/ubuntu/AYP/code/py_4/get_all_features.py:92: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['co_authors']=df.authors.apply(lambda x: [i['name'].lower().split(",") for i in x] )
/home/ubuntu/AYP/code/py_4/get_all_features.py:92: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.

Using pre-defined VAE FEATURES
Processing combination number 6 from 50
Using pre-defined VAE FEATURES
Processing combination number 7 from 50
Using pre-defined VAE FEATURES
Processing combination number 8 from 50
Using pre-defined VAE FEATURES
Processing combination number 9 from 50
Using pre-defined VAE FEATURES
Processing combination number 10 from 50


/home/ubuntu/AYP/code/py_4/get_all_features.py:92: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['co_authors']=df.authors.apply(lambda x: [i['name'].lower().split(",") for i in x] )
/home/ubuntu/AYP/code/py_4/get_all_features.py:92: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['co_authors']=df.authors.apply(lambda x: [i['name'].lower().split(",") for i in x] )
/home/ubuntu/AYP/code/py_4/get_all_features.py:92: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.

Using pre-defined VAE FEATURES
Processing combination number 11 from 50
Using pre-defined VAE FEATURES
Processing combination number 12 from 50
Using pre-defined VAE FEATURES
Processing combination number 13 from 50
Using pre-defined VAE FEATURES
Situation 0
Num Papers:  15
Num Clusters:  3
Num Unique Authors:  2
Precision:  0.7692307692307693
Recall:  0.6
              mis_integration  mis_separation
2 cluster(s)                2               2

-------------------

Situation 1
Num Papers:  15
Num Clusters:  1
Num Unique Authors:  2
Precision:  0.36
Recall:  0.6
              mis_integration  mis_separation
1 cluster(s)                2               2

-------------------



...

/home/ubuntu/anaconda3/envs/pytorch_latest_p36/lib/python3.6/site-packages/ipykernel/__main__.py:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/envs/pytorch_latest_p36/lib/python3.6/site-packages/ipykernel/__main__.py:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
/home/ubuntu/anaconda3/envs/pytorch_latest_p36/lib/python3.6/site-packages/ipykernel/__main__.py:23: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,co


Num Papers:  16
Num Clusters:  2
Num Unique Authors:  1
Precision:  1.0
Recall:  0.875
              mis_integration  mis_separation
2 cluster(s)                1               1

-------------------

Situation 9
Num Papers:  10
Num Clusters:  2
Num Unique Authors:  1
Precision:  1.0
Recall:  0.7
              mis_integration  mis_separation
2 cluster(s)                1               1

-------------------

Situation 10
Num Papers:  18
Num Clusters:  2
Num Unique Authors:  1
Precision:  1.0
Recall:  0.9444444444444444
              mis_integration  mis_separation
2 cluster(s)                1               1

-------------------

Situation 11
Num Papers:  8
Num Clusters:  1
Num Unique Authors:  1
Precision:  1.0
Recall:  1.0
              mis_integration  mis_separation
1 cluster(s)                1               1

-------------------

Situation 12
Num Papers:  34
Num Clusters:  1
Num Unique Authors:  1
Precision:  1.0
Recall:  1.0
              mis_integration  mis_separation
1 clu

/home/ubuntu/anaconda3/envs/pytorch_latest_p36/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/ubuntu/anaconda3/envs/pytorch_latest_p36/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/ubuntu/anaconda3/envs/pytorch_latest_p36/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/ubuntu/anaconda3

Situation 27
Num Papers:  18
Num Clusters:  1
Num Unique Authors:  1
Precision:  1.0
Recall:  1.0
              mis_integration  mis_separation
1 cluster(s)                1               1

-------------------

Situation 28
Num Papers:  14
Num Clusters:  1
Num Unique Authors:  1
Precision:  1.0
Recall:  1.0
              mis_integration  mis_separation
1 cluster(s)                1               1

-------------------

Situation 29
Num Papers:  13
Num Clusters:  3
Num Unique Authors:  1
Precision:  1.0
Recall:  0.8461538461538461
              mis_integration  mis_separation
3 cluster(s)                1               1

-------------------

Situation 30
Num Papers:  32
Num Clusters:  2
Num Unique Authors:  1
Precision:  1.0
Recall:  0.96875
              mis_integration  mis_separation
2 cluster(s)                1               1

-------------------

Situation 31
Num Papers:  11
Num Clusters:  1
Num Unique Authors:  1
Precision:  1.0
Recall:  1.0
              mis_integration  mis_

/home/ubuntu/anaconda3/envs/pytorch_latest_p36/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/ubuntu/anaconda3/envs/pytorch_latest_p36/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/ubuntu/anaconda3/envs/pytorch_latest_p36/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/ubuntu/anaconda3

In [139]:
# %%capture cap --no-stderr
for val in total_metric:
    case, f1, prec, rec, df_eval = val
    print("CASE: {}\t".format(case))
    print("\nF1-Score: {}\tTotal Precision: {}\tTotal Recall: {}".format(f1,prec,rec))
    print(df_eval)
    print("\n")
# with open('txt/test_scores_VAE_model.txt', 'w') as out:
#    out.write(cap.stdout)

CASE: 2_da_same	

F1-Score: 0.5695319709557539	Total Precision: 0.5454363497757279	Total Recall: 0.5958549222797926
                 1 cluster(s)  2 cluster(s)
mis_integration      0.333333      0.666667
mis_separation       0.333333      0.666667


CASE: 2_da_dif	

F1-Score: 0.6754482730849107	Total Precision: 0.6244798570217138	Total Recall: 0.7354758961681087
                 1 cluster(s)
mis_integration           1.0
mis_separation            1.0


CASE: 3_da	

F1-Score: 0.6267581413910321	Total Precision: 0.5822960943736362	Total Recall: 0.6785714285714284
                 1 cluster(s)
mis_integration           1.0
mis_separation            1.0


CASE: 1_da	

F1-Score: 0.9651593773165308	Total Precision: 1.0	Total Recall: 0.9326647564469914
                 3 cluster(s)
mis_integration           1.0
mis_separation            1.0




In [136]:
db__eps = np.linspace(2.0,2.5,5)
total_log = []
for db_eps in db__eps:
    y_hat_comb = pipeline_vae_db(df,authors=total_authors,eps=db_eps)
    f1, precision, recall, df_eval = metric_eval_2.get_metrics_many(y_hat_comb)
    total_log.append({"eps":db_eps,
                  "F1-Score":f1})    

Processing combination number 1 from 50
Using pre-defined VAE FEATURES
Processing combination number 2 from 50
Using pre-defined VAE FEATURES
Processing combination number 3 from 50
Using pre-defined VAE FEATURES
Processing combination number 4 from 50
Using pre-defined VAE FEATURES
Processing combination number 5 from 50


/home/ubuntu/AYP/code/py_4/get_all_features.py:92: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['co_authors']=df.authors.apply(lambda x: [i['name'].lower().split(",") for i in x] )
/home/ubuntu/AYP/code/py_4/get_all_features.py:92: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['co_authors']=df.authors.apply(lambda x: [i['name'].lower().split(",") for i in x] )
/home/ubuntu/AYP/code/py_4/get_all_features.py:92: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.

Using pre-defined VAE FEATURES
Processing combination number 6 from 50
Using pre-defined VAE FEATURES
Processing combination number 7 from 50
Using pre-defined VAE FEATURES
Processing combination number 8 from 50
Using pre-defined VAE FEATURES
Processing combination number 9 from 50
Using pre-defined VAE FEATURES
Processing combination number 10 from 50


/home/ubuntu/AYP/code/py_4/get_all_features.py:92: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['co_authors']=df.authors.apply(lambda x: [i['name'].lower().split(",") for i in x] )
/home/ubuntu/AYP/code/py_4/get_all_features.py:92: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['co_authors']=df.authors.apply(lambda x: [i['name'].lower().split(",") for i in x] )
/home/ubuntu/AYP/code/py_4/get_all_features.py:92: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.

Using pre-defined VAE FEATURES
Processing combination number 11 from 50
Using pre-defined VAE FEATURES
Processing combination number 12 from 50
Using pre-defined VAE FEATURES
Processing combination number 13 from 50
Using pre-defined VAE FEATURES
Processing combination number 14 from 50
Using pre-defined VAE FEATURES
Processing combination number 15 from 50


...

/home/ubuntu/anaconda3/envs/pytorch_latest_p36/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/ubuntu/anaconda3/envs/pytorch_latest_p36/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/ubuntu/anaconda3/envs/pytorch_latest_p36/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/ubuntu/a

Situation 87
Num Papers:  16
Num Clusters:  2
Num Unique Authors:  1
Precision:  1.0
Recall:  0.875
              mis_integration  mis_separation
2 cluster(s)                1               1

-------------------

Situation 88
Num Papers:  10
Num Clusters:  2
Num Unique Authors:  1
Precision:  1.0
Recall:  0.7
              mis_integration  mis_separation
2 cluster(s)                1               1

-------------------

Situation 89
Num Papers:  18
Num Clusters:  2
Num Unique Authors:  1
Precision:  1.0
Recall:  0.9444444444444444
              mis_integration  mis_separation
2 cluster(s)                1               1

-------------------

Situation 90
Num Papers:  8
Num Clusters:  1
Num Unique Authors:  1
Precision:  1.0
Recall:  1.0
              mis_integration  mis_separation
1 cluster(s)                1               1

-------------------

Situation 91
Num Papers:  34
Num Clusters:  1
Num Unique Authors:  1
Precision:  1.0
Recall:  1.0
              mis_integration  mis_sep

/home/ubuntu/anaconda3/envs/pytorch_latest_p36/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/ubuntu/anaconda3/envs/pytorch_latest_p36/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/ubuntu/anaconda3/envs/pytorch_latest_p36/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/ubuntu/anaconda3

Situation 106
Num Papers:  18
Num Clusters:  1
Num Unique Authors:  1
Precision:  1.0
Recall:  1.0
              mis_integration  mis_separation
1 cluster(s)                1               1

-------------------

Situation 107
Num Papers:  14
Num Clusters:  1
Num Unique Authors:  1
Precision:  1.0
Recall:  1.0
              mis_integration  mis_separation
1 cluster(s)                1               1

-------------------

Situation 108
Num Papers:  13
Num Clusters:  3
Num Unique Authors:  1
Precision:  1.0
Recall:  0.8461538461538461
              mis_integration  mis_separation
3 cluster(s)                1               1

-------------------

Situation 109
Num Papers:  32
Num Clusters:  2
Num Unique Authors:  1
Precision:  1.0
Recall:  0.96875
              mis_integration  mis_separation
2 cluster(s)                1               1

-------------------

Situation 110
Num Papers:  11
Num Clusters:  1
Num Unique Authors:  1
Precision:  1.0
Recall:  1.0
              mis_integration 

/home/ubuntu/anaconda3/envs/pytorch_latest_p36/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/ubuntu/anaconda3/envs/pytorch_latest_p36/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/ubuntu/anaconda3/envs/pytorch_latest_p36/lib/python3.6/site-packages/sklearn/metrics/_classification.py:1272: UndefinedMetricWarning: Recall is ill-defined and being set to 0.0 in labels with no true samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/home/ubuntu/anaconda3

In [137]:
total_log

[{'eps': 2.0, 'F1-Score': 0.77545455317688},
 {'eps': 2.125, 'F1-Score': 0.7751996240586895},
 {'eps': 2.25, 'F1-Score': 0.756972088863303},
 {'eps': 2.375, 'F1-Score': 0.7334007572033363},
 {'eps': 2.5, 'F1-Score': 0.7275372002809091}]